## Capstone course

Goal == Get a better understanding of indicators of accidents in Belgium.

### libraries to be imported

In [1]:
import pandas as pd
import numpy as np
import pandas_profiling as pp
from sklearn import preprocessing
from sklearn.preprocessing import LabelEncoder
from sklearn.linear_model import LinearRegression
from statsmodels.stats.outliers_influence import variance_inflation_factor
from sklearn.model_selection import train_test_split
from sklearn import linear_model
import statsmodels.api as sm
import matplotlib.pyplot as plt


#### Data to be imported

In [2]:
accidentdata = pd.read_excel("TF_ACCIDENTS_2019.xlsx")
accidentdata.head()

DT_DAY  DT_HOUR  CD_DAY_OF_WEEK TX_DAY_OF_WEEK_DESCR_FR  \
0 2019-09-27       18               5                Vendredi   
1 2019-11-20       12               3                Mercredi   
2 2019-07-15       14               1                   Lundi   
3 2019-04-20        2               6                  Samedi   
4 2019-10-25       12               5                Vendredi   

  TX_DAY_OF_WEEK_DESCR_NL  CD_BUILD_UP_AREA TX_BUILD_UP_AREA_DESCR_NL  \
0                 vrijdag               2.0       Buiten bebouwde kom   
1                woensdag               1.0       Binnen bebouwde kom   
2                 maandag               1.0       Binnen bebouwde kom   
3                zaterdag               2.0       Buiten bebouwde kom   
4                 vrijdag               2.0       Buiten bebouwde kom   

  TX_BUILD_UP_AREA_DESCR_FR  CD_COLL_TYPE  \
0        Hors agglomération           1.0   
1          En agglomération           4.0   
2          En agglomération           NaN   
3        Hors agglomération           1.0   
4        Hors agglomération           5.0   

                    TX_COLL_TYPE_DESCR_NL  ...   TX_PROV_DESCR_FR  \
0  Kettingbotsing (4 bestuurders of meer)  ...  Province d’Anvers   
1                             Langs opzij  ...  Province d’Anvers   
2                        Niet beschikbaar  ...  Province d’Anvers   
3  Kettingbotsing (4 bestuurders of meer)  ...  Province d’Anvers   
4                      Met een voetganger  ...  Province d’Anvers   

   CD_RGN_REFNIS TX_RGN_DESCR_NL  TX_RGN_DESCR_FR  MS_ACCT MS_ACCT_WITH_DEAD  \
0           2000   Vlaams Gewest  Région flamande        1                 1   
1           2000   Vlaams Gewest  Région flamande        1                 0   
2           2000   Vlaams Gewest  Région flamande        1                 0   
3           2000   Vlaams Gewest  Région flamande        1                 0   
4           2000   Vlaams Gewest  Région flamande        1                 0   

  MS_ACCT_WITH_DEAD_30_DAYS  MS_ACCT_WITH_MORY_INJ MS_ACCT_WITH_SERLY_INJ  \
0                         1                      0                      0   
1                         0                      0                      0   
2                         0                      0                      0   
3                         0                      0                      1   
4                         0                      0                      0   

  MS_ACCT_WITH_SLY_INJ  
0                    0  
1                    1  
2                    1  
3                    0  
4                    1  

[5 rows x 35 columns]

#### summary of the data

In [3]:
summary = accidentdata.profile_report()
summary

#### as we can see; there are a lot of unnecessary data_columns. Deleting the following duplicate or unnecessary data

In [4]:
accidentdata.drop(columns= ["CD_MUNTY_REFNIS", "TX_RGN_DESCR_NL","TX_MUNTY_DESCR_NL","TX_ADM_DSTR_DESCR_NL","TX_MUNTY_DESCR_FR", "CD_DSTR_REFNIS", "TX_ADM_DSTR_DESCR_FR", "CD_PROV_REFNIS", "TX_PROV_DESCR_FR", "CD_RGN_REFNIS", "TX_RGN_DESCR_FR", "MS_ACCT", "MS_ACCT_WITH_DEAD", "TX_DAY_OF_WEEK_DESCR_FR", "CD_BUILD_UP_AREA", "TX_BUILD_UP_AREA_DESCR_FR", "TX_COLL_TYPE_DESCR_FR", "CD_LIGHT_COND", "TX_LIGHT_COND_DESCR_FR","CD_ROAD_TYPE", "TX_ROAD_TYPE_DESCR_FR", "MS_ACCT_WITH_DEAD_30_DAYS"], inplace = True)

In [5]:
accidentdata.head()

DT_DAY  DT_HOUR  CD_DAY_OF_WEEK TX_DAY_OF_WEEK_DESCR_NL  \
0 2019-09-27       18               5                 vrijdag   
1 2019-11-20       12               3                woensdag   
2 2019-07-15       14               1                 maandag   
3 2019-04-20        2               6                zaterdag   
4 2019-10-25       12               5                 vrijdag   

  TX_BUILD_UP_AREA_DESCR_NL  CD_COLL_TYPE  \
0       Buiten bebouwde kom           1.0   
1       Binnen bebouwde kom           4.0   
2       Binnen bebouwde kom           NaN   
3       Buiten bebouwde kom           1.0   
4       Buiten bebouwde kom           5.0   

                    TX_COLL_TYPE_DESCR_NL  \
0  Kettingbotsing (4 bestuurders of meer)   
1                             Langs opzij   
2                        Niet beschikbaar   
3  Kettingbotsing (4 bestuurders of meer)   
4                      Met een voetganger   

                  TX_LIGHT_COND_DESCR_NL  \
0                    Bij klaarlichte dag   
1                    Bij klaarlichte dag   
2                    Bij klaarlichte dag   
3  Nacht, ontstoken openbare verlichting   
4                    Bij klaarlichte dag   

                    TX_ROAD_TYPE_DESCR_NL     TX_PROV_DESCR_NL  \
0                             Autosnelweg  Provincie Antwerpen   
1  Gewestweg, provincieweg of gemeenteweg  Provincie Antwerpen   
2  Gewestweg, provincieweg of gemeenteweg  Provincie Antwerpen   
3                             Autosnelweg  Provincie Antwerpen   
4  Gewestweg, provincieweg of gemeenteweg  Provincie Antwerpen   

   MS_ACCT_WITH_MORY_INJ  MS_ACCT_WITH_SERLY_INJ  MS_ACCT_WITH_SLY_INJ  
0                      0                       0                     0  
1                      0                       0                     1  
2                      0                       0                     1  
3                      0                       1                     0  
4                      0                       0                     1

In [6]:
for col in accidentdata.columns: ## replace all empty, 0 or null values with the NaN value.
    accidentdata[col].replace('', np.nan, inplace=True)
    accidentdata[col].replace('null', np.nan, inplace=True)

    
accidentdata.dropna( inplace=True)

In [7]:
summary = accidentdata.profile_report()
summary

In [8]:
accidentdata.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 27331 entries, 0 to 37497
Data columns (total 13 columns):
 #   Column                     Non-Null Count  Dtype         
---  ------                     --------------  -----         
 0   DT_DAY                     27331 non-null  datetime64[ns]
 1   DT_HOUR                    27331 non-null  int64         
 2   CD_DAY_OF_WEEK             27331 non-null  int64         
 3   TX_DAY_OF_WEEK_DESCR_NL    27331 non-null  object        
 4   TX_BUILD_UP_AREA_DESCR_NL  27331 non-null  object        
 5   CD_COLL_TYPE               27331 non-null  float64       
 6   TX_COLL_TYPE_DESCR_NL      27331 non-null  object        
 7   TX_LIGHT_COND_DESCR_NL     27331 non-null  object        
 8   TX_ROAD_TYPE_DESCR_NL      27331 non-null  object        
 9   TX_PROV_DESCR_NL           27331 non-null  object        
 10  MS_ACCT_WITH_MORY_INJ      27331 non-null  int64         
 11  MS_ACCT_WITH_SERLY_INJ     27331 non-null  int64         
 12  MS_A

#### model has been processed.

In [9]:
subseriesofaccidentdata= accidentdata[["MS_ACCT_WITH_MORY_INJ","MS_ACCT_WITH_SERLY_INJ", "MS_ACCT_WITH_SLY_INJ"]]

In [10]:
accidentsInjury=pd.get_dummies(subseriesofaccidentdata).idxmax(1)

accidentsInjuryPanda = pd.DataFrame(data=accidentsInjury, columns = ['accidentinjury'])
print(accidentsInjuryPanda.info())
result = pd.concat([accidentsInjuryPanda, accidentdata], axis=1)

<class 'pandas.core.frame.DataFrame'>
Int64Index: 27331 entries, 0 to 37497
Data columns (total 1 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   accidentinjury  27331 non-null  object
dtypes: object(1)
memory usage: 427.0+ KB
None


In [11]:
result.head()

accidentinjury     DT_DAY  DT_HOUR  CD_DAY_OF_WEEK  \
0   MS_ACCT_WITH_MORY_INJ 2019-09-27       18               5   
1    MS_ACCT_WITH_SLY_INJ 2019-11-20       12               3   
3  MS_ACCT_WITH_SERLY_INJ 2019-04-20        2               6   
4    MS_ACCT_WITH_SLY_INJ 2019-10-25       12               5   
5    MS_ACCT_WITH_SLY_INJ 2019-07-28       21               7   

  TX_DAY_OF_WEEK_DESCR_NL TX_BUILD_UP_AREA_DESCR_NL  CD_COLL_TYPE  \
0                 vrijdag       Buiten bebouwde kom           1.0   
1                woensdag       Binnen bebouwde kom           4.0   
3                zaterdag       Buiten bebouwde kom           1.0   
4                 vrijdag       Buiten bebouwde kom           5.0   
5                  zondag       Buiten bebouwde kom           7.0   

                    TX_COLL_TYPE_DESCR_NL  \
0  Kettingbotsing (4 bestuurders of meer)   
1                             Langs opzij   
3  Kettingbotsing (4 bestuurders of meer)   
4                      Met een voetganger   
5   Tegen een hindernis buiten de rijbaan   

                  TX_LIGHT_COND_DESCR_NL  \
0                    Bij klaarlichte dag   
1                    Bij klaarlichte dag   
3  Nacht, ontstoken openbare verlichting   
4                    Bij klaarlichte dag   
5                    Bij klaarlichte dag   

                    TX_ROAD_TYPE_DESCR_NL     TX_PROV_DESCR_NL  \
0                             Autosnelweg  Provincie Antwerpen   
1  Gewestweg, provincieweg of gemeenteweg  Provincie Antwerpen   
3                             Autosnelweg  Provincie Antwerpen   
4  Gewestweg, provincieweg of gemeenteweg  Provincie Antwerpen   
5  Gewestweg, provincieweg of gemeenteweg  Provincie Antwerpen   

   MS_ACCT_WITH_MORY_INJ  MS_ACCT_WITH_SERLY_INJ  MS_ACCT_WITH_SLY_INJ  
0                      0                       0                     0  
1                      0                       0                     1  
3                      0                       1                     0  
4                      0                       0                     1  
5                      0                       0                     1

In [12]:
result.drop(columns= ["MS_ACCT_WITH_MORY_INJ", "MS_ACCT_WITH_SERLY_INJ", "MS_ACCT_WITH_SLY_INJ", "TX_DAY_OF_WEEK_DESCR_NL"], inplace = True)

In [13]:
result.dtypes

accidentinjury                       object
DT_DAY                       datetime64[ns]
DT_HOUR                               int64
CD_DAY_OF_WEEK                        int64
TX_BUILD_UP_AREA_DESCR_NL            object
CD_COLL_TYPE                        float64
TX_COLL_TYPE_DESCR_NL                object
TX_LIGHT_COND_DESCR_NL               object
TX_ROAD_TYPE_DESCR_NL                object
TX_PROV_DESCR_NL                     object
dtype: object

#### encoding.

In [14]:
lb_encod = LabelEncoder()
result.loc[:,"accidentinjury_encoded"] = lb_encod.fit_transform(result.loc[:,"accidentinjury"])
result.loc[:,"TX_BUILD_UP_AREA_DESCR_NL_encoded"] = lb_encod.fit_transform(result.loc[:,"TX_BUILD_UP_AREA_DESCR_NL"])
result.loc[:,"TX_COLL_TYPE_DESCR_NL_encoded"] = lb_encod.fit_transform(result.loc[:,"TX_COLL_TYPE_DESCR_NL"])
result.loc[:,"TX_LIGHT_COND_DESCR_NL_encoded"] = lb_encod.fit_transform(result.loc[:,"TX_LIGHT_COND_DESCR_NL"])
result.loc[:,"TX_ROAD_TYPE_DESCR_NL_encoded"] = lb_encod.fit_transform(result.loc[:,"TX_ROAD_TYPE_DESCR_NL"])
result.loc[:,"TX_PROV_DESCR_NL_encoded"] = lb_encod.fit_transform(result.loc[:,"TX_PROV_DESCR_NL"])
result.head()

accidentinjury     DT_DAY  DT_HOUR  CD_DAY_OF_WEEK  \
0   MS_ACCT_WITH_MORY_INJ 2019-09-27       18               5   
1    MS_ACCT_WITH_SLY_INJ 2019-11-20       12               3   
3  MS_ACCT_WITH_SERLY_INJ 2019-04-20        2               6   
4    MS_ACCT_WITH_SLY_INJ 2019-10-25       12               5   
5    MS_ACCT_WITH_SLY_INJ 2019-07-28       21               7   

  TX_BUILD_UP_AREA_DESCR_NL  CD_COLL_TYPE  \
0       Buiten bebouwde kom           1.0   
1       Binnen bebouwde kom           4.0   
3       Buiten bebouwde kom           1.0   
4       Buiten bebouwde kom           5.0   
5       Buiten bebouwde kom           7.0   

                    TX_COLL_TYPE_DESCR_NL  \
0  Kettingbotsing (4 bestuurders of meer)   
1                             Langs opzij   
3  Kettingbotsing (4 bestuurders of meer)   
4                      Met een voetganger   
5   Tegen een hindernis buiten de rijbaan   

                  TX_LIGHT_COND_DESCR_NL  \
0                    Bij klaarlichte dag   
1                    Bij klaarlichte dag   
3  Nacht, ontstoken openbare verlichting   
4                    Bij klaarlichte dag   
5                    Bij klaarlichte dag   

                    TX_ROAD_TYPE_DESCR_NL     TX_PROV_DESCR_NL  \
0                             Autosnelweg  Provincie Antwerpen   
1  Gewestweg, provincieweg of gemeenteweg  Provincie Antwerpen   
3                             Autosnelweg  Provincie Antwerpen   
4  Gewestweg, provincieweg of gemeenteweg  Provincie Antwerpen   
5  Gewestweg, provincieweg of gemeenteweg  Provincie Antwerpen   

   accidentinjury_encoded  TX_BUILD_UP_AREA_DESCR_NL_encoded  \
0                       0                                  1   
1                       2                                  0   
3                       1                                  1   
4                       2                                  1   
5                       2                                  1   

   TX_COLL_TYPE_DESCR_NL_encoded  TX_LIGHT_COND_DESCR_NL_encoded  \
0                              2                               0   
1                              4                               0   
3                              2                               3   
4                              5                               0   
5                              6                               0   

   TX_ROAD_TYPE_DESCR_NL_encoded  TX_PROV_DESCR_NL_encoded  
0                              0                         0  
1                              1                         0  
3                              0                         0  
4                              1                         0  
5                              1                         0

In [15]:
result.drop(columns= ["accidentinjury", "TX_BUILD_UP_AREA_DESCR_NL", "TX_COLL_TYPE_DESCR_NL", "TX_LIGHT_COND_DESCR_NL","TX_ROAD_TYPE_DESCR_NL","TX_PROV_DESCR_NL", "DT_DAY"], inplace = True)

In [16]:
result.head()

DT_HOUR  CD_DAY_OF_WEEK  CD_COLL_TYPE  accidentinjury_encoded  \
0       18               5           1.0                       0   
1       12               3           4.0                       2   
3        2               6           1.0                       1   
4       12               5           5.0                       2   
5       21               7           7.0                       2   

   TX_BUILD_UP_AREA_DESCR_NL_encoded  TX_COLL_TYPE_DESCR_NL_encoded  \
0                                  1                              2   
1                                  0                              4   
3                                  1                              2   
4                                  1                              5   
5                                  1                              6   

   TX_LIGHT_COND_DESCR_NL_encoded  TX_ROAD_TYPE_DESCR_NL_encoded  \
0                               0                              0   
1                               0                              1   
3                               3                              0   
4                               0                              1   
5                               0                              1   

   TX_PROV_DESCR_NL_encoded  
0                         0  
1                         0  
3                         0  
4                         0  
5                         0

In [17]:
result.dtypes
for col in result.columns:
    result[col] = result[col].astype('category',copy=False)
    


In [18]:
result = preprocessing.StandardScaler().fit(result).transform(result)


In [19]:
CleanedUsableData = pd.DataFrame.from_records(result)
CleanedUsableData.columns = ["Hour", "Day", "collisionType", "Typeofaccidentinjury", "AreaDescription", "CollisionTypeDescription", "LightCondition", "RoadType", "Province"]
CleanedUsableData.head()
CleanedUsableData['Hour'] = CleanedUsableData.Hour.astype('category')
CleanedUsableData['Day'] = CleanedUsableData.Day.astype('category')
CleanedUsableData['collisionType'] = CleanedUsableData.collisionType.astype('category')
CleanedUsableData['Typeofaccidentinjury'] = CleanedUsableData.Typeofaccidentinjury.astype('category')
CleanedUsableData['AreaDescription'] = CleanedUsableData.AreaDescription.astype('category')
CleanedUsableData['CollisionTypeDescription'] = CleanedUsableData.CollisionTypeDescription.astype('category')
CleanedUsableData['LightCondition'] = CleanedUsableData.LightCondition.astype('category')
CleanedUsableData['RoadType'] = CleanedUsableData.RoadType.astype('category')
CleanedUsableData['Province'] = CleanedUsableData.Province.astype('category')
CleanedUsableData.dtypes


Hour                        category
Day                         category
collisionType               category
Typeofaccidentinjury        category
AreaDescription             category
CollisionTypeDescription    category
LightCondition              category
RoadType                    category
Province                    category
dtype: object

#### Preprocessing and normalization done. Data Can be found in CleanedUsableData.

#### I would like to know the relationship of Typeofaccidentinjury in comparison with the other variables. Linear Regression is the correct Approach.

In [20]:
x= CleanedUsableData[['Day', 'collisionType', 'AreaDescription', 'LightCondition', 'RoadType']]
y = CleanedUsableData[['Typeofaccidentinjury']]
print(x[0:5])
print(y[0:5])

        Day collisionType AreaDescription LightCondition  RoadType
0  0.562135     -1.849235        1.026941      -0.626179 -3.109767
1 -0.465572     -0.237496       -0.881621      -0.626179  0.303745
2  1.075988     -1.849235        1.026941       1.642291 -3.109767
3  0.562135      0.299750        1.026941      -0.626179  0.303745
4  1.589842      1.374243        1.026941      -0.626179  0.303745
  Typeofaccidentinjury
0            -4.737319
1             0.340955
2            -2.198182
3             0.340955
4             0.340955


In [21]:
X_train, X_test, y_train, y_test = train_test_split(
x, y, test_size=0.33, random_state=42)

In [22]:
regressionmodel = linear_model.LinearRegression()

In [23]:
regressionmodel.fit(X_train, y_train)
print(regressionmodel.coef_)

[[-0.018296   -0.07222498 -0.06654727 -0.02779452  0.01257229]]


In [24]:
y_hat= regressionmodel.predict(X_test)
print(y_hat[0:5])

[[-0.25171543]
 [ 0.07697034]
 [ 0.04637246]
 [-0.17584851]
 [-0.0406342 ]]


In [25]:
print(y_test[0:5])

      Typeofaccidentinjury
1190              0.340955
22891             0.340955
6620              0.340955
23277             0.340955
6480              0.340955


In [26]:
print('Variance score: %.2f' % regressionmodel.score(x, y))

Variance score: 0.01


In [27]:
X2 = sm.add_constant(x)
est = sm.OLS(y, X2)
est2 = est.fit()
print(est2.summary())

                             OLS Regression Results                             
Dep. Variable:     Typeofaccidentinjury   R-squared:                       0.014
Model:                              OLS   Adj. R-squared:                  0.014
Method:                   Least Squares   F-statistic:                     77.28
Date:                  Fri, 02 Oct 2020   Prob (F-statistic):           9.49e-81
Time:                          08:59:43   Log-Likelihood:                -38589.
No. Observations:                 27331   AIC:                         7.719e+04
Df Residuals:                     27325   BIC:                         7.724e+04
Df Model:                             5                                         
Covariance Type:              nonrobust                                         
                      coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------
const             2.96

#### R-value is very low. P chosen as cut-off point = 0.05. Every value with a p-value <0.05 has an impact on the model.

#### let's drop all columns which do not have an impact on the model. (This will have an impact on the R-value of the model).

In [28]:
def calc_vif(X):

    # Calculating VIF
    vif = pd.DataFrame()
    vif["variables"] = X.columns
    vif["VIF"] = [variance_inflation_factor(X.values, i) for i in range(X.shape[1])]

    return(vif)

In [29]:
calc_vif(x)

variables       VIF
0              Day  1.018614
1    collisionType  1.028497
2  AreaDescription  1.110191
3   LightCondition  1.031190
4         RoadType  1.110690